In [3]:
import os
import numpy as np
from collections import deque

In [6]:
# take a nii file
data_path = "../Data/"
example_filename = os.path.join(data_path, 'volume-covid19-A-0000.nii.gz')

# load image
import nibabel as nib
img = nib.load(example_filename)

# show shapes
img.shape

(512, 512, 341)

In [69]:
# growing function
class RegionGrow3D():
    """
    documentation
    """

    def __init__(self, images, masks, upperThreshold, lowerThreshold, neighborMode):
        self.images = images
        self.masks = masks
        self.outputMask = np.zeros_like(self.images)
        self.upperThreshold = upperThreshold
        self.lowerThreshold = lowerThreshold
        self.neighborMode = neighborMode
        self.queue = deque()

    def main(self, seed):

        newItem = np.zeros(3)
        neighbors = np.zeros((26,3))
        newItem = seed

        self.outputMask[newItem[0], newItem[1], newItem[2]] = 1
        self.queue.append((seed[0], seed[1], seed[2]))

        while len(self.queue) != 0:
            print(self.queue)
            newItem = self.queue.pop()
            if self.neighborMode == "26n":
                neighbors = [[newItem[0]-1, newItem[1]-1, newItem[2]-1],   [newItem[0]-1, newItem[1]-1, newItem[2]],   [newItem[0]-1, newItem[1]-1, newItem[2]+1],
                             [newItem[0]-1, newItem[1], newItem[2]-1],     [newItem[0]-1, newItem[1], newItem[2]],     [newItem[0]-1, newItem[1], newItem[2]+1],
                             [newItem[0]-1, newItem[1]+1, newItem[2]-1],   [newItem[0]-1, newItem[1]+1, newItem[2]],   [newItem[0]-1, newItem[1]+1, newItem[2]+1],
                             [newItem[0], newItem[1]-1, newItem[2]-1],     [newItem[0], newItem[1]-1, newItem[2]],     [newItem[0], newItem[1]-1, newItem[2]+1],
                             [newItem[0], newItem[1], newItem[2]-1],       [newItem[0], newItem[1], newItem[2]+1],     [newItem[0], newItem[1]+1, newItem[2]-1],
                             [newItem[0], newItem[1]+1, newItem[2]],       [newItem[0], newItem[1]+1, newItem[2]+1],   [newItem[0]+1, newItem[1]-1, newItem[2]-1],
                             [newItem[0]+1, newItem[1]-1, newItem[2]],     [newItem[0]+1, newItem[1]-1, newItem[2]+1], [newItem[0]+1, newItem[1], newItem[2]-1],
                             [newItem[0]+1, newItem[1], newItem[2]],       [newItem[0]+1, newItem[1], newItem[2]+1],   [newItem[0]+1, newItem[1]+1, newItem[2]-1],
                             [newItem[0]+1, newItem[1]+1, newItem[2]],     [newItem[0]+1, newItem[1]+1, newItem[2]+1]]
                for neighbor in neighbors:
                    self.checkNeighbour(neighbor[0], neighbor[1], neighbor[2])
            elif self.neighborMode == "6n":
                print("WEEE")
                self.checkNeighbour(newItem[0], newItem[1], newItem[2]-1)
                self.checkNeighbour(newItem[0], newItem[1], newItem[2]+1)
                self.checkNeighbour(newItem[0], newItem[1]-1, newItem[2])
                self.checkNeighbour(newItem[0], newItem[1]+1, newItem[2])
                self.checkNeighbour(newItem[0]-1, newItem[1], newItem[2])
                self.checkNeighbour(newItem[0]+1, newItem[1], newItem[2])
        return self.outputMask

    # todo check this 513 if it is meaningful
    def checkNeighbour(self, x, y, z):
        print(x,y,z)
        if (x < 512 and y < 512 and z < 341
            and x > -1 and y > -1 and z > -1
            and self.masks[x,y,z] == 1):
            intensity = self.images[x, y, z]
            print(intensity)
            if self.isIntensityAcceptable(intensity) and self.outputMask[x,y,z] == 0:
                print("WEEEE")
                self.outputMask[x,y,z] = 1
                self.queue.append((x, y, z))

    def isIntensityAcceptable(self, intensity):
        if ((intensity < self.upperThreshold) and (intensity > self.lowerThreshold)):
            return True
        else:
          return False

In [76]:
# todo insert seed and edges

image = img.get_fdata()
seed = [421,135,170]
print(seed)
mask = np.ones(image.shape)
#print(mask)
rg = RegionGrow3D(image,mask,-904,-1104,"6n")
out = rg.main(seed)

[421, 135, 170]
deque([(421, 135, 170)])
WEEE
421 135 169
-1008.0
WEEEE
421 135 171
-1020.0
WEEEE
421 134 170
-1010.0
WEEEE
421 136 170
-1000.0
WEEEE
420 135 170
-1006.0
WEEEE
422 135 170
-1008.0
WEEEE
deque([(421, 135, 169), (421, 135, 171), (421, 134, 170), (421, 136, 170), (420, 135, 170), (422, 135, 170)])
WEEE
422 135 169
-989.0
WEEEE
422 135 171
-1019.0
WEEEE
422 134 170
-1005.0
WEEEE
422 136 170
-1010.0
WEEEE
421 135 170
-1004.0
423 135 170
-1010.0
WEEEE
deque([(421, 135, 169), (421, 135, 171), (421, 134, 170), (421, 136, 170), (420, 135, 170), (422, 135, 169), (422, 135, 171), (422, 134, 170), (422, 136, 170), (423, 135, 170)])
WEEE
423 135 169
-999.0
WEEEE
423 135 171
-1015.0
WEEEE
423 134 170
-1006.0
WEEEE
423 136 170
-1016.0
WEEEE
422 135 170
-1008.0
424 135 170
-1013.0
WEEEE
deque([(421, 135, 169), (421, 135, 171), (421, 134, 170), (421, 136, 170), (420, 135, 170), (422, 135, 169), (422, 135, 171), (422, 134, 170), (422, 136, 170), (423, 135, 169), (423, 135, 171), (423, 13

-1009.0
WEEEE
deque([(421, 135, 169), (421, 135, 171), (421, 134, 170), (421, 136, 170), (420, 135, 170), (422, 135, 169), (422, 135, 171), (422, 134, 170), (422, 136, 170), (423, 135, 169), (423, 135, 171), (423, 134, 170), (423, 136, 170), (424, 135, 169), (424, 135, 171), (424, 134, 170), (424, 136, 170), (425, 135, 169), (425, 135, 171), (425, 134, 170), (425, 136, 170), (426, 135, 169), (426, 135, 171), (426, 134, 170), (426, 136, 170), (427, 135, 169), (427, 135, 171), (427, 134, 170), (427, 136, 170), (428, 135, 169), (428, 135, 171), (428, 134, 170), (428, 136, 170), (429, 135, 169), (429, 135, 171), (429, 134, 170), (429, 136, 170), (430, 135, 169), (430, 135, 171), (430, 134, 170), (430, 136, 170), (431, 135, 169), (431, 135, 171), (431, 134, 170), (431, 136, 170), (432, 135, 169), (432, 135, 171), (432, 134, 170), (432, 136, 170), (433, 135, 169), (433, 135, 171), (433, 134, 170), (433, 136, 170), (434, 135, 169), (434, 135, 171), (434, 134, 170), (434, 136, 170), (435, 135,

WEEEE
485 142 170
-2048.0
485 144 170
-1010.0
WEEEE
484 143 170
-992.0
486 143 170
-2048.0
deque([(421, 135, 169), (421, 135, 171), (421, 134, 170), (421, 136, 170), (420, 135, 170), (422, 135, 169), (422, 135, 171), (422, 134, 170), (422, 136, 170), (423, 135, 169), (423, 135, 171), (423, 134, 170), (423, 136, 170), (424, 135, 169), (424, 135, 171), (424, 134, 170), (424, 136, 170), (425, 135, 169), (425, 135, 171), (425, 134, 170), (425, 136, 170), (426, 135, 169), (426, 135, 171), (426, 134, 170), (426, 136, 170), (427, 135, 169), (427, 135, 171), (427, 134, 170), (427, 136, 170), (428, 135, 169), (428, 135, 171), (428, 134, 170), (428, 136, 170), (429, 135, 169), (429, 135, 171), (429, 134, 170), (429, 136, 170), (430, 135, 169), (430, 135, 171), (430, 134, 170), (430, 136, 170), (431, 135, 169), (431, 135, 171), (431, 134, 170), (431, 136, 170), (432, 135, 169), (432, 135, 171), (432, 134, 170), (432, 136, 170), (433, 135, 169), (433, 135, 171), (433, 134, 170), (433, 136, 170), (

WEEEE
470 155 170
-1004.0
deque([(421, 135, 169), (421, 135, 171), (421, 134, 170), (421, 136, 170), (420, 135, 170), (422, 135, 169), (422, 135, 171), (422, 134, 170), (422, 136, 170), (423, 135, 169), (423, 135, 171), (423, 134, 170), (423, 136, 170), (424, 135, 169), (424, 135, 171), (424, 134, 170), (424, 136, 170), (425, 135, 169), (425, 135, 171), (425, 134, 170), (425, 136, 170), (426, 135, 169), (426, 135, 171), (426, 134, 170), (426, 136, 170), (427, 135, 169), (427, 135, 171), (427, 134, 170), (427, 136, 170), (428, 135, 169), (428, 135, 171), (428, 134, 170), (428, 136, 170), (429, 135, 169), (429, 135, 171), (429, 134, 170), (429, 136, 170), (430, 135, 169), (430, 135, 171), (430, 134, 170), (430, 136, 170), (431, 135, 169), (431, 135, 171), (431, 134, 170), (431, 136, 170), (432, 135, 169), (432, 135, 171), (432, 134, 170), (432, 136, 170), (433, 135, 169), (433, 135, 171), (433, 134, 170), (433, 136, 170), (434, 135, 169), (434, 135, 171), (434, 134, 170), (434, 136, 170)

WEEEE
434 156 170
-1016.0
WEEEE
433 155 170
-1006.0
WEEEE
435 155 170
-1007.0
deque([(421, 135, 169), (421, 135, 171), (421, 134, 170), (421, 136, 170), (420, 135, 170), (422, 135, 169), (422, 135, 171), (422, 134, 170), (422, 136, 170), (423, 135, 169), (423, 135, 171), (423, 134, 170), (423, 136, 170), (424, 135, 169), (424, 135, 171), (424, 134, 170), (424, 136, 170), (425, 135, 169), (425, 135, 171), (425, 134, 170), (425, 136, 170), (426, 135, 169), (426, 135, 171), (426, 134, 170), (426, 136, 170), (427, 135, 169), (427, 135, 171), (427, 134, 170), (427, 136, 170), (428, 135, 169), (428, 135, 171), (428, 134, 170), (428, 136, 170), (429, 135, 169), (429, 135, 171), (429, 134, 170), (429, 136, 170), (430, 135, 169), (430, 135, 171), (430, 134, 170), (430, 136, 170), (431, 135, 169), (431, 135, 171), (431, 134, 170), (431, 136, 170), (432, 135, 169), (432, 135, 171), (432, 134, 170), (432, 136, 170), (433, 135, 169), (433, 135, 171), (433, 134, 170), (433, 136, 170), (434, 135, 169

...

deque([(421, 135, 169), (421, 135, 171), (421, 134, 170), (421, 136, 170), (420, 135, 170), (422, 135, 169), (422, 135, 171), (422, 134, 170), (422, 136, 170), (423, 135, 169), (423, 135, 171), (423, 134, 170), (423, 136, 170), (424, 135, 169), (424, 135, 171), (424, 134, 170), (424, 136, 170), (425, 135, 169), (425, 135, 171), (425, 134, 170), (425, 136, 170), (426, 135, 169), (426, 135, 171), (426, 134, 170), (426, 136, 170), (427, 135, 169), (427, 135, 171), (427, 134, 170), (427, 136, 170), (428, 135, 169), (428, 135, 171), (428, 134, 170), (428, 136, 170), (429, 135, 169), (429, 135, 171), (429, 134, 170), (429, 136, 170), (430, 135, 169), (430, 135, 171), (430, 134, 170), (430, 136, 170), (431, 135, 169), (431, 135, 171), (431, 134, 170), (431, 136, 170), (432, 135, 169), (432, 135, 171), (432, 134, 170), (432, 136, 170), (433, 135, 169), (433, 135, 171), (433, 134, 170), (433, 136, 170), (434, 135, 169), (434, 135, 171), (434, 134, 170), (434, 136, 170), (435, 135, 169), (435, 1

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




471 169 185
-999.0
473 169 185
-997.0
WEEEE
deque([(421, 135, 169), (421, 135, 171), (421, 134, 170), (421, 136, 170), (420, 135, 170), (422, 135, 169), (422, 135, 171), (422, 134, 170), (422, 136, 170), (423, 135, 169), (423, 135, 171), (423, 134, 170), (423, 136, 170), (424, 135, 169), (424, 135, 171), (424, 134, 170), (424, 136, 170), (425, 135, 169), (425, 135, 171), (425, 134, 170), (425, 136, 170), (426, 135, 169), (426, 135, 171), (426, 134, 170), (426, 136, 170), (427, 135, 169), (427, 135, 171), (427, 134, 170), (427, 136, 170), (428, 135, 169), (428, 135, 171), (428, 134, 170), (428, 136, 170), (429, 135, 169), (429, 135, 171), (429, 134, 170), (429, 136, 170), (430, 135, 169), (430, 135, 171), (430, 134, 170), (430, 136, 170), (431, 135, 169), (431, 135, 171), (431, 134, 170), (431, 136, 170), (432, 135, 169), (432, 135, 171), (432, 134, 170), (432, 136, 170), (433, 135, 169), (433, 135, 171), (433, 134, 170), (433, 136, 170), (434, 135, 169), (434, 135, 171), (434, 134, 17

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



KeyboardInterrupt: 

In [71]:
#image[410:430, 125:135, 160:180]

In [ ]:
unique, counts = np.unique(out, return_counts=True)

In [ ]:
unique

In [ ]:
counts

In [75]:
image.shape


(512, 512, 341)